In [21]:
import pandas as pd
import numpy as np
import datetime

#import xgboost as xgb

from keras.models import Sequential
from keras.layers import Dense
from keras import layers
from keras.layers import Dropout

import matplotlib.pyplot as plt
from tensorflow import keras

In [22]:

from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import cross_val_score
import torch
import transformers as ppb
import warnings
warnings.filterwarnings('ignore')

In [3]:
from transformers import (
   BertTokenizerFast,
   AutoModelForMaskedLM,
   AutoModelForTokenClassification,
)

tokenizer = BertTokenizerFast.from_pretrained('bert-base-chinese')
model = AutoModelForMaskedLM.from_pretrained('ckiplab/albert-tiny-chinese') # or other models above

In [4]:
cutword = pd.read_pickle("C:/Users/Junhao/Google Drive/wechat data/cut001.pkl")
cutword1 = cutword.head(100).wordsCut
cutword2 = cutword.head(100).title

In [23]:
tokenized = cutword2.apply((lambda x: tokenizer.encode(x, add_special_tokens=True)))

In [25]:
max_len = 0
for i in tokenized.values:
    if len(i) > max_len:
        max_len = len(i)

padded = np.array([i + [0]*(max_len-len(i)) for i in tokenized.values])

In [8]:
attention_mask = np.where(padded != 0, 1, 0)
attention_mask.shape

(100, 52)

In [9]:
input_ids = torch.tensor(padded)  
attention_mask = torch.tensor(attention_mask)

In [13]:
input_ids
input_ids = torch.tensor(input_ids).to(torch.int64)

In [14]:
with torch.no_grad():
    last_hidden_states = model(input_ids, attention_mask=attention_mask)

In [15]:
features = last_hidden_states[0][:,0,:].numpy()

In [18]:
likeCount = cutword.head(100).likeCount

In [19]:
train_features, test_features, train_labels, test_labels = train_test_split(features, likeCount)

In [26]:

from statsmodels.formula.api  import ols
import statsmodels.api as sm

#linear regression with all variables
results = sm.OLS(train_labels.astype(float), train_features.astype(float)).fit()
results.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              likeCount   R-squared:                       1.000
Model:                            OLS   Adj. R-squared:                    nan
Method:                 Least Squares   F-statistic:                       nan
Date:                Sat, 23 Jan 2021   Prob (F-statistic):                nan
Time:                        12:52:53   Log-Likelihood:                 1644.6
No. Observations:                  75   AIC:                            -3139.
Df Residuals:                       0   BIC:                            -2965.
Df Model:                          74                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
x1             0.4816        inf          0        nan         nan         nan
x2            -0.6307        inf         -0        nan         nan         nan
x3            -0.4105        inf         -0        nan         nan         nan
x4             0.1529        inf          0        nan         nan         nan
x5             0.3354        inf          0        nan         nan         nan
x6            -0.2173        inf         -0        nan         nan         nan
x7            -0.7229        inf         -0        nan         nan         nan
x8             0.5240        inf          0        nan         nan         nan
x9             0.1878        inf          0        nan         nan         nan
x10           -0.0702        inf         -0        nan         nan         nan
x11           -0.4722        inf         -0        nan         nan         nan
x12            0.1868        inf          0        nan         nan         nan
x13           -0.0938        inf         -0        nan         nan         nan
x14           -0.2241        inf         -0        nan         nan         nan
x15            0.3508        inf          0        nan         nan         nan
x16            0.1274        inf          0        nan         nan         nan
x17           -0.5894        inf         -0        nan         nan         nan
x18           -0.6257        inf         -0        nan         nan         nan
x19            0.2841        inf          0        nan         nan         nan
x20            0.5114        inf          0        nan         nan         nan
x21           -0.3655        inf         -0        nan         nan         nan
x22           -0.3689        inf         -0        nan         nan         nan
x23           -0.3994        inf         -0        nan         nan         nan
x24           -0.4747        inf         -0        nan         nan         nan
x25            0.0575        inf          0        nan         nan         nan
x26           -0.2057        inf         -0        nan         nan         nan
x27           -0.5721        inf         -0        nan         nan         nan
x28            0.5016        inf          0        nan         nan         nan
x29           -0.1797        inf         -0        nan         nan         nan
x30           -0.5182        inf         -0        nan         nan         nan
x31            0.0784        inf          0        nan         nan         nan
x32            0.0589        inf          0        nan         nan         nan
x33           -0.2501        inf         -0        nan         nan         nan
x34           -0.2172        inf         -0        nan         nan         nan
x35            0.1529        inf          0        nan         nan         nan
x36           -0.6718        inf         -0        nan         nan         nan
x3

In [28]:
from sklearn.linear_model import LinearRegression
reg = LinearRegression().fit(train_features, train_labels)
reg.score(train_features, train_labels)

0.9999999998765461

In [32]:
from sklearn.metrics import mean_squared_error, r2_score
preds = reg.predict(test_features)

rmse = np.sqrt(mean_squared_error(test_labels.astype(float), preds))
print("RMSE: %f" % (rmse))

mean_squared_error(test_labels, preds)


RMSE: 469.087203


220042.80409784854

In [30]:
from sklearn.dummy import DummyRegressor
clf = DummyRegressor()

scores = cross_val_score(clf, train_features, train_labels)
print("Dummy classifier score: %0.3f (+/- %0.2f)" % (scores.mean(), scores.std() * 2))

Dummy classifier score: -0.225 (+/- 0.74)
